In [ ]:
:dep polars = { version = "x", features = ["lazy", "describe"]}
:dep glob

#### Описание данных

В папке Data находится информация о студентах. Всего 10 групп студентов. Файлы делятся на две категории:
    * Students_info_i - информация о студентах из группы i
    * Students_marks_i - оценки студентов из группы i за экзамены

#### Задание 1. 

Соберите всю информацию о студентах в одну таблицу df. В получившейся таблице должна быть информация и оценки всех студентов из всех групп. Напечатайте несколько строк таблицы для демонстрации результата.¶

In [30]:
use glob::glob;
use polars::prelude::*;
use std::path::Path;

let infos_csv = "../../HW01/Data/Students_info_*.csv";
let mut infos_vec = vec![];

for path in glob(infos_csv).unwrap() {
    if let Ok(csv) = path {
        
        let lf = LazyCsvReader::new(csv)
            .finish()
            .unwrap();
        infos_vec.push(lf);
    }
}
    
let marks_csv = "../../HW01/Data/Students_marks_*.csv";
let mut marks_vec = vec![];

for path in glob(marks_csv).unwrap() {
    if let Ok(csv) = path {
        let lf = LazyCsvReader::new(csv)
            .finish()
            .unwrap();
        marks_vec.push(lf);
    }
}

let df_info = infos_vec.into_iter()
            .reduce(
                |acc, lf| concat(
                    [acc.clone(), lf.clone()], 
                    UnionArgs::default()
                ).unwrap())
            .unwrap();

let df_marks = marks_vec.into_iter()
            .reduce(
                |acc, lf| concat(
                    [acc.clone(), lf.clone()], 
                    UnionArgs::default()
                ).unwrap())
            .unwrap();

let df = df_info.join(
                    df_marks, 
                    [col("index")],
                    [col("index")],
                    JoinArgs::default(),
                )
                .collect()
                .unwrap();
df

shape: (1_000, 10)
┌───────┬────────┬─────────────────┬────────────────┬───┬─────────┬────────────┬─────────┬─────────┐
│ index ┆ gender ┆ race/ethnicity  ┆ parental level ┆ … ┆ group   ┆ math score ┆ reading ┆ writing │
│ ---   ┆ ---    ┆ ---             ┆ of education   ┆   ┆ ---     ┆ ---        ┆ score   ┆ score   │
│ i64   ┆ str    ┆ str             ┆ ---            ┆   ┆ str     ┆ i64        ┆ ---     ┆ ---     │
│       ┆        ┆                 ┆ str            ┆   ┆         ┆            ┆ i64     ┆ i64     │
╞═══════╪════════╪═════════════════╪════════════════╪═══╪═════════╪════════════╪═════════╪═════════╡
│ 0     ┆ female ┆ group B         ┆ bachelor's     ┆ … ┆ group1  ┆ 72         ┆ 72      ┆ 74      │
│       ┆        ┆                 ┆ degree         ┆   ┆         ┆            ┆         ┆         │
│ 1     ┆ female ┆ group C         ┆ some college   ┆ … ┆ group1  ┆ 69         ┆ 90      ┆ 88      │
│ 2     ┆ female ┆ group B         ┆ master's       ┆ … ┆ group1  ┆ 90  

#### Задание 2. 

Удалите столбец index у полученной таблицы. Напечатайте первые 10 строк таблицы. Выведите на экран размеры полученной таблицы.

In [31]:
// если не работает, перезапустите предыдущую ячейку
let df = df.drop("index").unwrap();
df

shape: (1_000, 9)
┌────────┬───────────────┬───────────────┬───────────────┬───┬─────────┬───────┬─────────┬─────────┐
│ gender ┆ race/ethnicit ┆ parental      ┆ lunch         ┆ … ┆ group   ┆ math  ┆ reading ┆ writing │
│ ---    ┆ y             ┆ level of      ┆ ---           ┆   ┆ ---     ┆ score ┆ score   ┆ score   │
│ str    ┆ ---           ┆ education     ┆ str           ┆   ┆ str     ┆ ---   ┆ ---     ┆ ---     │
│        ┆ str           ┆ ---           ┆               ┆   ┆         ┆ i64   ┆ i64     ┆ i64     │
│        ┆               ┆ str           ┆               ┆   ┆         ┆       ┆         ┆         │
╞════════╪═══════════════╪═══════════════╪═══════════════╪═══╪═════════╪═══════╪═════════╪═════════╡
│ female ┆ group B       ┆ bachelor's    ┆ standard      ┆ … ┆ group1  ┆ 72    ┆ 72      ┆ 74      │
│        ┆               ┆ degree        ┆               ┆   ┆         ┆       ┆         ┆         │
│ female ┆ group C       ┆ some college  ┆ standard      ┆ … ┆ group1  ┆ 

#### Задание 3. 

Выведите на экран статистические характеристики числовых столбцов таблицы (минимум, максимум, среднее значение, стандартное отклонение)

In [ ]:
// похоже, они убрали этот метод
df.describe(None).unwrap();

Error: no method named `describe` found for struct `polars::prelude::DataFrame` in the current scope

#### Задание 4. 

Проверьте, есть ли в таблице пропущенные значения

In [ ]:
df.isna().any()

gender                         False
race/ethnicity                 False
parental level of education    False
lunch                          False
test preparation course        False
group                          False
math score                     False
reading score                  False
writing score                  False
dtype: bool

#### Задание 5. 

Выведите на экран средние баллы студентов по каждому предмету (math, reading, writing)

In [ ]:
print(f'Math = {df["math score"].mean()}')
print(f'Reading = {df["reading score"].mean()}')
print(f'Writing = {df["writing score"].mean()}')


Math = 66.089
Reading = 69.169
Writing = 68.054


#### Задание 6. 

Как зависят оценки от того, проходил ли студент курс для подготовки к сдаче экзамена (test preparation course)? Выведите на экран для каждого предмета в отдельности средний балл студентов, проходивших курс для подготовки к экзамену и не проходивших курс.

In [ ]:
no_prep_m = df[(df["test preparation course"]) == 'none']["math score"].mean()
print(f"No preparation course, math: {no_prep_m}")

no_prep_r = df[(df["test preparation course"]) == 'none']["reading score"].mean()
print(f"No preparation course, reading: {no_prep_r}")

no_prep_w = df[(df["test preparation course"]) == 'none']["writing score"].mean()
print(f"No preparation course, writing: {no_prep_w}")

prep_m = df[(df["test preparation course"]) == 'completed']["math score"].mean()
print(f"Preparation course, math: {prep_m}")

prep_r = df[(df["test preparation course"]) == 'completed']["reading score"].mean()
print(f"Preparation course, reading: {prep_r}")

prep_w = df[(df["test preparation course"]) == 'completed']["writing score"].mean()
print(f"Preparation course, writing: {prep_w}")



No preparation course, math: 64.0778816199377
No preparation course, reading: 66.53426791277259
No preparation course, writing: 64.50467289719626
Preparation course, math: 69.69553072625699
Preparation course, reading: 73.89385474860335
Preparation course, writing: 74.41899441340782


#### Задание 7. 

Выведите на экран все различные значения из столбца lunch.

In [ ]:
print(df["lunch"].unique())

['standard' 'free/reduced']


#### Задание 8. 

Переименуйте колонку "parental level of education" в "education", а "test preparation course" в "test preparation" с помощью метода pandas rename
https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.rename.html

In [ ]:
df.rename(columns={"parental level of education": "education", 
                    "test preparation course": "test preparation"},
                    inplace=True)
df.sample(5)

gender race/ethnicity           education         lunch test preparation  \
915  female        group E        some college      standard             none   
685    male        group C         high school      standard             none   
987    male        group E    some high school      standard        completed   
525    male        group D        some college      standard        completed   
193    male        group C  associate's degree  free/reduced        completed   

       group  math score  reading score  writing score  
915  group10          68             70             66  
685   group5          70             74             71  
987  group10          81             75             76  
525   group7         100             97             99  
193   group1          43             45             50

**Зафиксируем минимальный балл для сдачи экзамена**

In [ ]:
passmark = 50

#### Задание 9. 

Ответьте на вопросы:

    * Какая доля студентов сдала экзамен по математике (passmark > 50)?
    * Какая доля студентов, проходивших курс подготовки к экзамену, сдала экзамен по математике?
    * Какая доля женщин, не проходивших курс подготовки к экзамену, не сдала экзамен по математике? 

In [ ]:
passed = df[df["math score"] > passmark]['math score'].count()
print(f"Passed = {100 * passed / df['math score'].count()}%")

passed_and_prep = df[(df["math score"] > passmark) & (df["test preparation"] == 'completed')]['math score'].count()
preped = df[df["test preparation"] == 'completed']['math score'].count()
print(f"Доля проходивших тест и сдавших из проходивших курс: {100 * passed_and_prep / preped}%")
print(f"Доля проходивших тест и сдавших из всех: {100 * passed_and_prep / df['math score'].count()}%")

women_no_prep = df[(df["gender"] == "female") & (df["test preparation"] == "none") & (df["math score"] < passmark)]
women_no_prep = women_no_prep["math score"].count()
women = df[df["gender"] == "female"]["gender"].count()
print(f"Доля женщин, не проходивших курс подготовки к экзамену, которые не сдали экзамен, из всех женщин: {100 * women_no_prep / women}%")
print(f"Доля женщин, не проходивших курс подготовки к экзамену, которые не сдали экзамен, из всех: {100 * women_no_prep / df["math score"].count()}%")


Passed = 85.0%
Доля проходивших тест и сдавших из проходивших курс: 90.78212290502793%
Доля проходивших тест и сдавших из всех: 32.5%
Доля женщин, не проходивших курс подготовки к экзамену, которые не сдали экзамен, из всех женщин: 13.513513513513514%
Доля женщин, не проходивших курс подготовки к экзамену, которые не сдали экзамен, из всех: 7.0%


#### Задание 10. 

С помощью groupby выполните задания ниже. Также выведите время выполнения каждого из заданий.

    * Для каждой этнической группы выведите средний балл за экзамен по чтению
    * Для каждого уровня образования выведите минимальный балл за экзамен по письму

In [ ]:
print(df.groupby('race/ethnicity')['reading score'].mean())
df.groupby('education')['writing score'].min()

race/ethnicity
group A    64.674157
group B    67.352632
group C    69.103448
group D    70.030534
group E    73.028571
Name: reading score, dtype: float64


education
associate's degree    35
bachelor's degree     38
high school           15
master's degree       46
some college          19
some high school      10
Name: writing score, dtype: int64

#### Задание 11.

Выполните задание 10 с помощью циклов. Сравните время выполнения.

In [ ]:
group_a = 0
group_b = 0
group_c = 0
group_d = 0
group_e = 0

df_a = df[df['race/ethnicity'] == 'group A']['reading score']
df_b = df[df['race/ethnicity'] == 'group B']['reading score']
df_c = df[df['race/ethnicity'] == 'group C']['reading score']
df_d = df[df['race/ethnicity'] == 'group D']['reading score']
df_e = df[df['race/ethnicity'] == 'group E']['reading score']

for score in df_a:
    group_a += score
for score in df_b:
    group_b += score
for score in df_c:
    group_c += score
for score in df_d:
    group_d += score
for score in df_e:
    group_e += score

print(f'Group A: {group_a/df_a.count()}')
print(f'Group B: {group_b/df_b.count()}')
print(f'Group C: {group_c/df_c.count()}')
print(f'Group D: {group_d/df_d.count()}')
print(f'Group E: {group_e/df_e.count()}')

df_ad = df[df['education'] == "associate's degree"]['writing score']
df_bd = df[df['education'] == "bachelor's degree"]['writing score']
df_hs = df[df['education'] == "high school"]['writing score']
df_md = df[df['education'] == "master's degree"]['writing score']
df_sc = df[df['education'] == "some college"]['writing score']
df_shs = df[df['education'] == "some high school"]['writing score']

score_ad =  101
score_bd =  101
score_hs =  101
score_md =  101
score_sc =  101
score_shs = 101

for score in df_ad:
    if score < score_ad:
        score_ad = score
for score in df_bd:
    if score < score_bd:
        score_bd = score
for score in df_hs:
    if score < score_hs:
        score_hs = score
for score in df_md:
    if score < score_md:
        score_md = score
for score in df_sc:
    if score < score_sc:
        score_sc = score
for score in df_shs:
    if score < score_shs:
        score_shs = score
        
print()
print(f"Associate's degree: {score_ad}")
print(f"Bachelor's degree: {score_bd}")
print(f"High school: {score_hs}")
print(f"Master's degree: {score_md}")
print(f"Some college: {score_sc}")
print(f"Some high school: {score_shs}")

Group A: 64.67415730337079
Group B: 67.35263157894737
Group C: 69.10344827586206
Group D: 70.03053435114504
Group E: 73.02857142857142

Associate's degree: 35
Bachelor's degree: 38
High school: 15
Master's degree: 46
Some college: 19
Some high school: 10


In [ ]:
%%timeit

print(df.groupby('race/ethnicity')['reading score'].mean())
df.groupby('education')['writing score'].min()

race/ethnicity
group A    64.674157
group B    67.352632
group C    69.103448
group D    70.030534
group E    73.028571
Name: reading score, dtype: float64
race/ethnicity
group A    64.674157
group B    67.352632
group C    69.103448
group D    70.030534
group E    73.028571
Name: reading score, dtype: float64
race/ethnicity
group A    64.674157
group B    67.352632
group C    69.103448
group D    70.030534
group E    73.028571
Name: reading score, dtype: float64
race/ethnicity
group A    64.674157
group B    67.352632
group C    69.103448
group D    70.030534
group E    73.028571
Name: reading score, dtype: float64
race/ethnicity
group A    64.674157
group B    67.352632
group C    69.103448
group D    70.030534
group E    73.028571
Name: reading score, dtype: float64
race/ethnicity
group A    64.674157
group B    67.352632
group C    69.103448
group D    70.030534
group E    73.028571
Name: reading score, dtype: float64
race/ethnicity
group A    64.674157
group B    67.352632
group C

In [ ]:
%%timeit

group_a = 0
group_b = 0
group_c = 0
group_d = 0
group_e = 0

df_a = df[df['race/ethnicity'] == 'group A']['reading score']
df_b = df[df['race/ethnicity'] == 'group B']['reading score']
df_c = df[df['race/ethnicity'] == 'group C']['reading score']
df_d = df[df['race/ethnicity'] == 'group D']['reading score']
df_e = df[df['race/ethnicity'] == 'group E']['reading score']

for score in df_a:
    group_a += score
for score in df_b:
    group_b += score
for score in df_c:
    group_c += score
for score in df_d:
    group_d += score
for score in df_e:
    group_e += score

print(f'Group A: {group_a/df_a.count()}')
print(f'Group B: {group_b/df_b.count()}')
print(f'Group C: {group_c/df_c.count()}')
print(f'Group D: {group_d/df_d.count()}')
print(f'Group E: {group_e/df_e.count()}')

df_ad = df[df['education'] == "associate's degree"]['writing score']
df_bd = df[df['education'] == "bachelor's degree"]['writing score']
df_hs = df[df['education'] == "high school"]['writing score']
df_md = df[df['education'] == "master's degree"]['writing score']
df_sc = df[df['education'] == "some college"]['writing score']
df_shs = df[df['education'] == "some high school"]['writing score']

score_ad =  101
score_bd =  101
score_hs =  101
score_md =  101
score_sc =  101
score_shs = 101

for score in df_ad:
    if score < score_ad:
        score_ad = score
for score in df_bd:
    if score < score_bd:
        score_bd = score
for score in df_hs:
    if score < score_hs:
        score_hs = score
for score in df_md:
    if score < score_md:
        score_md = score
for score in df_sc:
    if score < score_sc:
        score_sc = score
for score in df_shs:
    if score < score_shs:
        score_shs = score
        
print()
print(f"Associate's degree: {score_ad}")
print(f"Bachelor's degree: {score_bd}")
print(f"High school: {score_hs}")
print(f"Master's degree: {score_md}")
print(f"Some college: {score_sc}")
print(f"Some high school: {score_shs}")

Group A: 64.67415730337079
Group B: 67.35263157894737
Group C: 69.10344827586206
Group D: 70.03053435114504
Group E: 73.02857142857142

Associate's degree: 35
Bachelor's degree: 38
High school: 15
Master's degree: 46
Some college: 19
Some high school: 10
Group A: 64.67415730337079
Group B: 67.35263157894737
Group C: 69.10344827586206
Group D: 70.03053435114504
Group E: 73.02857142857142

Associate's degree: 35
Bachelor's degree: 38
High school: 15
Master's degree: 46
Some college: 19
Some high school: 10
Group A: 64.67415730337079
Group B: 67.35263157894737
Group C: 69.10344827586206
Group D: 70.03053435114504
Group E: 73.02857142857142

Associate's degree: 35
Bachelor's degree: 38
High school: 15
Master's degree: 46
Some college: 19
Some high school: 10
Group A: 64.67415730337079
Group B: 67.35263157894737
Group C: 69.10344827586206
Group D: 70.03053435114504
Group E: 73.02857142857142

Associate's degree: 35
Bachelor's degree: 38
High school: 15
Master's degree: 46
Some college: 19
S

In [ ]:
# 1.61 мс циклами
# 397 мкс встроенными методами
# встроенными методами в 4 раза быстрее

#### Задание 12. 

Выведите на экран средние баллы студентов по каждому предмету в зависимости от пола и уровня образования. То есть должно получиться количество групп, равных 2 * (число уровней образования), и для каждой такой группы выыведите средний балл по каждому из предметов.

Это можно сделать с помощью сводных таблиц (pivot_table). Дополнительно о них почитать можно тут:

https://www.kaggle.com/kamilpolak/tutorial-how-to-use-pivot-table-in-pandas

In [ ]:
import numpy as np
df.head()

pivot = pd.pivot_table(df, index=['education', 'gender'], aggfunc={'reading score': "mean", 'writing score': "mean", 'math score': "mean"})
pivot

math score  reading score  writing score
education          gender                                          
associate's degree female   65.250000      74.120690      74.000000
                   male     70.764151      67.433962      65.405660
bachelor's degree  female   68.349206      77.285714      78.380952
                   male     70.581818      68.090909      67.654545
high school        female   59.351064      68.202128      66.691489
                   male     64.705882      61.480392      58.539216
master's degree    female   66.500000      76.805556      77.638889
                   male     74.826087      73.130435      72.608696
some college       female   65.406780      73.550847      74.050847
                   male     69.009259      64.990741      63.148148
some high school   female   59.296703      69.109890      68.285714
                   male     67.840909      64.693182      61.375000

#### Задание 13. 

Сколько студентов успешно сдали экзамен по математике?

Создайте новый столбец в таблице df под названием Math_PassStatus и запишите в него F, если студент не сдал экзамен по математике (балл за экзамен < passmark), и P иначе.

Посчитайте количество студентов, сдавших и не сдавших экзамен по математике.

Сделайте аналогичные шаги для экзаменов по чтению и письму.

In [ ]:
df.head()

df["Math_PassStatus"] = df['math score'].apply(lambda s: "F" if s < passmark else "P")
df["Reading_PassStatus"] = df['reading score'].apply(lambda s: "F" if s < passmark else "P")
df["Writing_PassStatus"] = df['writing score'].apply(lambda s: "F" if s < passmark else "P")
df.sample(10)

gender race/ethnicity           education         lunch test preparation  \
505    male        group C    some high school      standard             none   
356    male        group A  associate's degree      standard             none   
302  female        group C  associate's degree      standard        completed   
36     male        group B    some high school      standard        completed   
759    male        group D    some high school      standard             none   
216  female        group E  associate's degree  free/reduced        completed   
92   female        group B    some high school      standard             none   
679    male        group E  associate's degree      standard             none   
342  female        group B         high school      standard        completed   
108    male        group D         high school  free/reduced        completed   

      group  math score  reading score  writing score Math_PassStatus  \
505  group7          75             72             62               P   
356  group4          63             61             61               P   
302  group4          67             84             81               P   
36   group2          51             54             41               P   
759  group6          73             66             62               P   
216  group3          83             86             88               P   
92   group2          62             64             66               P   
679  group5          76             71             67               P   
342  group4          69             76             74               P   
108  group1          64             64             67               P   

    Reading_PassStatus Writing_PassStatus  
505                  P                  P  
356                  P                  P  
302                  P                  P  
36                   P                  F  
759                  P                  P  
216                  P                  P  
92                   P                  P  
679                  P                  P  
342                  P                  P  
108                  P                  P

#### Задание 14. 

Сколько студентов успешно сдали все экзамены?

Создайте столбец OverAll_PassStatus и запишите в него для каждого студента 'F', если студент не сдал хотя бы один из трех экзаменов, а иначе 'P'.

Посчитайте количество студентов, которые сдали все экзамены.

In [ ]:
def get_mark(x, y, z):
    if x == "F" or y == "F" or z == "F":
        return "F"
    return "P"

df["OverAll_PassStatus"] = df.apply(lambda x: get_mark(x['Math_PassStatus'], x['Reading_PassStatus'], x['Writing_PassStatus']), axis=1)

df.sample(10)


gender race/ethnicity           education         lunch test preparation  \
543  female        group E         high school      standard        completed   
867    male        group B  associate's degree      standard             none   
744  female        group D     master's degree      standard             none   
793  female        group E         high school      standard             none   
787  female        group C   bachelor's degree  free/reduced             none   
528    male        group D        some college  free/reduced             none   
282  female        group D   bachelor's degree  free/reduced             none   
757    male        group C     master's degree  free/reduced             none   
905    male        group D        some college      standard             none   
774  female        group E         high school      standard             none   

       group  math score  reading score  writing score Math_PassStatus  \
543   group7          74             79             80               P   
867   group9          61             42             41               P   
744   group6          64             63             66               P   
793   group6          74             76             73               P   
787   group6          44             63             62               F   
528   group7          49             57             46               F   
282   group3          73             79             84               P   
757   group6          61             67             66               P   
905  group10          88             77             77               P   
774   group6          74             81             71               P   

    Reading_PassStatus Writing_PassStatus OverAll_PassStatus  
543                  P                  P                  P  
867                  F                  F                  F  
744                  P                  P                  P  
793                  P                  P                  P  
787                  P                  P                  F  
528                  P                  F                  F  
282                  P                  P                  P  
757                  P                  P                  P  
905                  P                  P                  P  
774                  P                  P                  P

#### Задание 15. 

Переведем баллы в оценки

*Система перевода баллов в оценки*

        [90;100] = A
        [80;90) = B
        [70;80) = C
        [60;70) = D
        [50;60) = E
        [0;50) = F (Fail)

Создайте вспомогательную функцию, которая будет по среднему баллу за три экзамена выставлять оценку студенту по данным выше критериям.

Создайте столбец Grade и запишите в него оценку каждого студента.

Выведите количество студентов, получивших каждую из оценок.

In [ ]:
def GetGrade(m, r, w):
    a = np.mean([m, r, w])
    if a < 50:
        return "F"
    if a < 60:
        return "E"
    if a < 70:
        return "D"
    if a < 80:
        return "C"
    if a < 90:
        return "B"
    return "A"

df["Final Mark"] = df.apply(lambda x: GetGrade(x["math score"], x["reading score"], x["writing score"]), axis=1)

df.sample(10)

gender race/ethnicity           education         lunch test preparation  \
272  female        group D  associate's degree  free/reduced             none   
306    male        group E        some college      standard        completed   
145    male        group B  associate's degree      standard             none   
279    male        group B   bachelor's degree  free/reduced             none   
33   female        group C        some college      standard        completed   
320  female        group C         high school  free/reduced        completed   
962  female        group E  associate's degree      standard             none   
483  female        group C  associate's degree      standard        completed   
481  female        group B     master's degree      standard             none   
392    male        group E        some college      standard             none   

       group  math score  reading score  writing score Math_PassStatus  \
272   group3          47             53             58               F   
306   group4          99             87             81               P   
145   group1          65             54             57               P   
279   group3          73             56             57               P   
33    group2          75             81             84               P   
320   group4          67             79             84               P   
962  group10         100            100            100               P   
483   group8          52             59             62               P   
481   group8          77             90             84               P   
392   group4          76             67             67               P   

    Reading_PassStatus Writing_PassStatus OverAll_PassStatus Final Mark  
272                  P                  P                  F          E  
306                  P                  P                  P          B  
145                  P                  P                  P          E  
279                  P                  P                  P          D  
33                   P                  P                  P          B  
320                  P                  P                  P          C  
962                  P                  P                  P          A  
483                  P                  P                  P          E  
481                  P                  P                  P          B  
392                  P                  P                  P          C